In [164]:
import pandas as pd
import numpy as np

In [165]:
def encode_gender(gender):
    if gender == 'M':
        return 1
    elif gender == 'F':
        return 0
    else:
        return None
    
def calculate_age(birth_date):
    birth_year = int(birth_date[:4])
    birth_month = int(birth_date[5:7])
    birth_day = int(birth_date[8:])
    
    reference_year = 2024
    reference_month = 5
    reference_day = 1
    
    age = reference_year - birth_year - ((reference_month, reference_day) < (birth_month, birth_day))
    return age

In [166]:
df1 = pd.read_csv('data/vital_sign_his.csv')
#df1 = df1.dropna(subset=['SBP', 'DBP', 'HR', 'RR', 'BT'])

df1['AGE'] = df1['생년월일'].apply(calculate_age)
df1['GENDER'] = df1['성별'].apply(encode_gender)

vital_sign_his_mean = df1.groupby('환자번호').mean().reset_index()
vital_sign_his_mean.to_csv('data/vital_sign_his_mean.csv', index=False)

In [167]:
df2 = pd.read_csv('data/vital_sign_emr.csv')
df2['SBP'] = pd.to_numeric(df2['SBP'], errors='coerce')
df2['BT'] = pd.to_numeric(df2['BT'], errors='coerce')
#df2 = df2.dropna(subset=['SBP', 'DBP', 'HR', 'RR', 'BT'])

df2['AGE'] = df2['생년월일'].apply(calculate_age)
df2['GENDER'] = df2['성별'].apply(encode_gender)

vital_sign_emr_mean = df2.groupby('환자번호').mean().reset_index()
vital_sign_emr_mean.to_csv('data/vital_sign_emr_mean.csv', index=False)

In [168]:
vital_sign_combined = pd.concat([vital_sign_his_mean, vital_sign_emr_mean], ignore_index=False)
vital_sign_combined.to_csv('data/vital_sign_combined.csv', index=False)

In [169]:
df3 = pd.read_csv('data/result_his.csv')
df3['검사결과'] = df3['검사결과'].str.replace(r'mg/dL', '', regex=True).astype(float)
result_his_mean = df3.groupby('환자번호').mean().reset_index()
result_his_mean.to_csv('data/result_his_mean.csv', index=False)

In [170]:
df4 = pd.read_csv('data/result_emr.csv')
df4['검사결과'] = df4['검사결과'].str.replace(r'<', '', regex=True)
df4['검사결과'] = df4['검사결과'].str.replace(r'mg/dL', '', regex=True).astype(float)
result_emr_mean = df4.groupby('환자번호').mean().reset_index()
result_emr_mean.to_csv('data/result_emr_mean.csv', index=False)

In [171]:
result_combined = pd.concat([result_his_mean, result_emr_mean], ignore_index=False)
result_combined = result_combined.groupby('환자번호').mean().reset_index()
result_combined.to_csv('data/result_combined.csv', index=False)

In [172]:
duplicated_columns = set(result_combined.columns) & set(vital_sign_combined.columns)
duplicated_columns.discard('환자번호')  
print(duplicated_columns)

{'INCLUSION', 'EXCLUSION', 'VISIBLE_STONE_CT', 'PTBD', 'CT', 'DUCT_DILIATATION', 'EUS', 'ERCP', 'PANCREATITIS', 'PTGBD', 'MRCP', 'REAL_STONE'}


In [173]:
def check_columns(df1, df2, columns):
    for col in columns:
        col_result = col + '_result'
        col_vital = col + '_vital'
        
        # NaN을 같은 값으로 간주하여 병합
        df_merged = pd.merge(df1, df2, on='환자번호', how='outer', suffixes=('_result', '_vital'))
        df_merged.replace({np.nan: 'NaN'}, inplace=True)

        # 중복된 컬럼의 값이 일치하는지 확인
        match = df_merged[col_result] == df_merged[col_vital]

        # 일치하지 않는 환자번호와 해당 값 출력
        if match.all():
            print(f"모든 환자번호에 대해 {col} 값이 일치합니다.")
        else:
            mismatched_indices = df_merged[~match].index
            print(f"일부 환자번호에 대해 {col} 값이 일치하지 않습니다.")
            for index in mismatched_indices:
                patient_id = df_merged.loc[index, '환자번호']
                col_result_value = df_merged.loc[index, col_result]
                col_vital_value = df_merged.loc[index, col_vital]
                print(f"환자번호 {patient_id}: 결과 파일 {col} 값 - {col_result_value}, vital_sign 파일 {col} 값 - {col_vital_value}")

# 중복된 컬럼에 대해 검사 수행
check_columns(result_combined, vital_sign_combined, duplicated_columns)

모든 환자번호에 대해 INCLUSION 값이 일치합니다.
모든 환자번호에 대해 EXCLUSION 값이 일치합니다.
모든 환자번호에 대해 VISIBLE_STONE_CT 값이 일치합니다.
모든 환자번호에 대해 PTBD 값이 일치합니다.
모든 환자번호에 대해 CT 값이 일치합니다.
모든 환자번호에 대해 DUCT_DILIATATION 값이 일치합니다.
모든 환자번호에 대해 EUS 값이 일치합니다.
모든 환자번호에 대해 ERCP 값이 일치합니다.
모든 환자번호에 대해 PANCREATITIS 값이 일치합니다.
모든 환자번호에 대해 PTGBD 값이 일치합니다.
모든 환자번호에 대해 MRCP 값이 일치합니다.
모든 환자번호에 대해 REAL_STONE 값이 일치합니다.


In [174]:
result_combined.drop(columns=duplicated_columns, inplace=True)
vital_result_combined = pd.merge(vital_sign_combined, result_combined, on='환자번호', how='outer')
vital_result_combined.to_csv('data/vital_result_combined.csv', index=False)
vital_result_combined

환자번호  INCLUSION  EXCLUSION   CT  DUCT_DILIATATION  VISIBLE_STONE_CT  \
0    10001862        1.0        3.0  1.0               1.0               1.0   
1    10003102        1.0        0.0  1.0               1.0               0.0   
2    10003613        1.0        3.0  1.0               1.0               1.0   
3    10004457        1.0        0.0  1.0               1.0               0.0   
4    10011840        1.0        0.0  1.0               1.0               0.0   
..        ...        ...        ...  ...               ...               ...   
192  10332716        1.0        0.0  1.0               0.0               0.0   
193  10335454        1.0        3.0  1.0               1.0               1.0   
194  10335585        1.0        0.0  1.0               1.0               0.0   
195  10337095        1.0        0.0  1.0               0.0               0.0   
196  10339455        1.0        0.0  1.0               1.0               0.0   

     REAL_STONE  PANCREATITIS  ERCP  PTBD  ...  EUS  MRCP         SBP  \
0           1.0           0.0   0.0   1.0  ...  NaN   NaN   97.566667   
1           0.0           0.0   0.0   0.0  ...  0.0   1.0  114.166667   
2           1.0           0.0   1.0   NaN  ...  NaN   1.0  126.800000   
3           1.0           0.0   1.0   NaN  ...  1.0   NaN  121.000000   
4           0.0           1.0   0.0   NaN  ...  NaN   1.0  124.714286   
..          ...           ...   ...   ...  ...  ...   ...         ...   
192         0.0           0.0   1.0   NaN  ...  NaN   NaN  104.000000   
193         1.0           1.0   1.0   NaN  ...  NaN   NaN  117.888889   
194         0.0           0.0   0.0   NaN  ...  NaN   1.0  102.428571   
195         0.0           1.0   0.0   NaN  ...  1.0   NaN  108.833333   
196         0.0           0.0   0.0   NaN  ...  1.0   NaN  103.888889   

           DBP         HR         RR         BT   AGE  GENDER       검사결과  
0    55.166667  90.741935  24.954545  37.617391  74.0     1.0   3.500000  
1    70.666667  90.333333  17.666667  37.477778  66.0     1.0   3.350000  
2    59.600000  65.000000  19.600000  37.590909  94.0     0.0   0.800000  
3    72.000000  76.000000  18.000000  37.000000  92.0     1.0   0.600000  
4    76.857143  70.166667  18.666667  36.590000  61.0     1.0   1.300000  
..         ...        ...        ...        ...   ...     ...        ...  
192  63.750000  66.500000  20.000000  36.425000  32.0     0.0  18.105000  
193  61.333333  77.250000  23.788889  36.811111  93.0     0.0  22.891944  
194  67.714286  81.428571  18.428571  37.686667  59.0     1.0  17.683036  
195  69.833333  78.166667  22.166667  37.507692  81.0     0.0  20.591190  
196  76.333333  88.000000  20.111111  37.566667  78.0     0.0  19.467056  

[197 rows x 21 columns]

In [175]:
duplicated_columns = set(df1.columns) & set(df2.columns)
duplicated_columns.discard('환자번호')  
print(duplicated_columns)

{'DUCT_DILIATATION', 'DBP', 'FIRST_VISIT_DATE', 'RR', 'INCLUSION', 'EXCLUSION', 'PTBD', '성별', 'PTGBD_DATE', 'EUS', 'PTGBD', 'ERCP_DATE', 'DATA_END', 'HR', 'ANATOMY', 'SBP', 'CT', '측정일시', 'AGE', 'CT_DATE', '생년월일', 'PTBD_DATE', 'MRCP_DATE', 'VISIBLE_STONE_CT', 'GENDER', 'EUS_DATE', 'CT판독', 'DATA_START', 'ERCP', 'PANCREATITIS', 'BT', 'MRCP', 'REAL_STONE'}


In [176]:
check_columns(df1, df2, duplicated_columns)

일부 환자번호에 대해 DUCT_DILIATATION 값이 일치하지 않습니다.
환자번호 10001862: 결과 파일 DUCT_DILIATATION 값 - 1.0, vital_sign 파일 DUCT_DILIATATION 값 - NaN
환자번호 10001862: 결과 파일 DUCT_DILIATATION 값 - 1.0, vital_sign 파일 DUCT_DILIATATION 값 - NaN
환자번호 10001862: 결과 파일 DUCT_DILIATATION 값 - 1.0, vital_sign 파일 DUCT_DILIATATION 값 - NaN
환자번호 10001862: 결과 파일 DUCT_DILIATATION 값 - 1.0, vital_sign 파일 DUCT_DILIATATION 값 - NaN
환자번호 10001862: 결과 파일 DUCT_DILIATATION 값 - 1.0, vital_sign 파일 DUCT_DILIATATION 값 - NaN
환자번호 10001862: 결과 파일 DUCT_DILIATATION 값 - 1.0, vital_sign 파일 DUCT_DILIATATION 값 - NaN
환자번호 10001862: 결과 파일 DUCT_DILIATATION 값 - 1.0, vital_sign 파일 DUCT_DILIATATION 값 - NaN
환자번호 10001862: 결과 파일 DUCT_DILIATATION 값 - 1.0, vital_sign 파일 DUCT_DILIATATION 값 - NaN
환자번호 10001862: 결과 파일 DUCT_DILIATATION 값 - 1.0, vital_sign 파일 DUCT_DILIATATION 값 - NaN
환자번호 10001862: 결과 파일 DUCT_DILIATATION 값 - 1.0, vital_sign 파일 DUCT_DILIATATION 값 - NaN
환자번호 10001862: 결과 파일 DUCT_DILIATATION 값 - 1.0, vital_sign 파일 DUCT_DILIATATION 값 - NaN
환자번호 100018

In [177]:
file1_path = 'data/bileduct_data_20240508b_uppercase.csv'
file2_path = 'data/vital_result_combined.csv'

df1 = pd.read_csv(file1_path)
df2 = pd.read_csv(file2_path)

df1.drop(['FIRST_VISIT_ DATE', 'CT_DATE', 'ERCP_DATE', 'PTBD_DATE', 'PTGBD_DATE', 'EUS_DATE', 'MRCP_DATE', 'DATA_START', 'DATA_END', 'ERCP.1', 'PTBD.1'], axis=1, inplace=True)

In [178]:
all_combined = pd.merge(df1, df2, on='환자번호', how='inner', suffixes=('_result', '_vital'))

common_columns = ['INCLUSION', 'EXCLUSION', 'PTBD', 'VISIBLE_STONE_CT', 'CT', 'EUS', 'PTGBD', 'ERCP', 'PANCREATITIS', 'MRCP', 'REAL_STONE']
for col in common_columns:
    result_col = col + '_result'
    vital_col = col + '_vital'
    all_combined[col] = all_combined[result_col].fillna(all_combined[vital_col])

all_combined.drop(columns=[col + '_result' for col in common_columns] + [col + '_vital' for col in common_columns], inplace=True)
all_combined.to_csv('data/all_combined.csv', index=False)